
# 网格搜索与交叉验证的自定义重拟合策略

本示例展示了如何通过交叉验证优化分类器，
这是使用 :class:`~sklearn.model_selection.GridSearchCV` 对象
在仅包含一半可用标记数据的开发集上完成的。

然后在专门的评估集上测量所选超参数和训练模型的性能，
该评估集在模型选择步骤中未被使用。

有关模型选择工具的更多详细信息，请参见
`cross_validation` 和 `grid_search` 部分。


## The dataset

我们将使用 `digits` 数据集。目标是对手写数字图像进行分类。
为了便于理解，我们将问题转化为二分类问题：目标是识别一个数字是否为 `8` 。



In [ ]:
from sklearn import datasets

digits = datasets.load_digits()

为了在图像上训练分类器，我们需要将它们展平为向量。
每个8x8像素的图像需要转换为64像素的向量。
因此，我们将得到一个形状为 `(n_images, n_pixels)` 的最终数据数组。



In [ ]:
n_samples = len(digits.images)
X = digits.images.reshape((n_samples, -1))
y = digits.target == 8
print(
    f"The number of images is {X.shape[0]} and each image contains {X.shape[1]} pixels"
)

正如介绍中所述，数据将被分成大小相等的训练集和测试集。



In [ ]:
from sklearn.model_selection import train_test_split

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.5, random_state=0)

## 定义我们的网格搜索策略

我们将通过在训练集的折叠上搜索最佳超参数来选择分类器。为此，我们需要定义选择最佳候选者的评分标准。



In [ ]:
scores = ["precision", "recall"]

我们还可以定义一个函数传递给 :class:`~sklearn.model_selection.GridSearchCV` 实例的 `refit` 参数。该函数将实现自定义策略，从 :class:`~sklearn.model_selection.GridSearchCV` 的 `cv_results_` 属性中选择最佳候选者。一旦候选者被选中，它将自动由 :class:`~sklearn.model_selection.GridSearchCV` 实例重新拟合。

在这里，策略是筛选出在精度和召回率方面表现最好的模型。从选定的模型中，我们最终选择预测速度最快的模型。请注意，这些自定义选择是完全任意的。



In [ ]:
import pandas as pd


def print_dataframe(filtered_cv_results):
    """过滤后的数据框美化打印"""
    for mean_precision, std_precision, mean_recall, std_recall, params in zip(
        filtered_cv_results["mean_test_precision"],
        filtered_cv_results["std_test_precision"],
        filtered_cv_results["mean_test_recall"],
        filtered_cv_results["std_test_recall"],
        filtered_cv_results["params"],
    ):
        print(
            f"precision: {mean_precision:0.3f} (±{std_precision:0.03f}),"
            f" recall: {mean_recall:0.3f} (±{std_recall:0.03f}),"
            f" for {params}"
        )
    print()


def refit_strategy(cv_results):
    """定义选择最佳估计器的策略。

这里定义的策略是过滤掉所有低于0.98精度阈值的结果，按召回率对剩余结果进行排序，并保留召回率在最佳值一个标准差范围内的所有模型。一旦选定这些模型，我们可以选择预测最快的模型。

Parameters
----------
cv_results : dict of numpy (masked) ndarrays
    `GridSearchCV` 返回的交叉验证结果。

返回
-------
best_index : int
    最佳估计器在 `cv_results` 中的索引。
"""
    # 打印不同评分的网格搜索信息
    precision_threshold = 0.98

    cv_results_ = pd.DataFrame(cv_results)
    print("All grid-search results:")
    print_dataframe(cv_results_)

    # 过滤掉所有低于阈值的结果
    high_precision_cv_results = cv_results_[
        cv_results_["mean_test_precision"] > precision_threshold
    ]

    print(f"Models with a precision higher than {precision_threshold}:")
    print_dataframe(high_precision_cv_results)

    high_precision_cv_results = high_precision_cv_results[
        [
            "mean_score_time",
            "mean_test_recall",
            "std_test_recall",
            "mean_test_precision",
            "std_test_precision",
            "rank_test_recall",
            "rank_test_precision",
            "params",
        ]
    ]

    # 选择召回率表现最好的模型（在最佳模型的1个标准差范围内）
    best_recall_std = high_precision_cv_results["mean_test_recall"].std()
    best_recall = high_precision_cv_results["mean_test_recall"].max()
    best_recall_threshold = best_recall - best_recall_std

    high_recall_cv_results = high_precision_cv_results[
        high_precision_cv_results["mean_test_recall"] > best_recall_threshold
    ]
    print(
        "Out of the previously selected high precision models, we keep all the\n"
        "the models within one standard deviation of the highest recall model:"
    )
    print_dataframe(high_recall_cv_results)

    # 从最佳候选者中选择最快的模型进行预测
    fastest_top_recall_high_precision_index = high_recall_cv_results[
        "mean_score_time"
    ].idxmin()

    print(
        "\nThe selected final model is the fastest to predict out of the previously\n"
        "selected subset of best models based on precision and recall.\n"
        "Its scoring time is:\n\n"
        f"{high_recall_cv_results.loc[fastest_top_recall_high_precision_index]}"
    )

    return fastest_top_recall_high_precision_index

## 调整超参数

一旦我们定义了选择最佳模型的策略，我们就定义超参数的值并创建网格搜索实例：



In [ ]:
from sklearn.model_selection import GridSearchCV
from sklearn.svm import SVC

tuned_parameters = [
    {"kernel": ["rbf"], "gamma": [1e-3, 1e-4], "C": [1, 10, 100, 1000]},
    {"kernel": ["linear"], "C": [1, 10, 100, 1000]},
]

grid_search = GridSearchCV(
    SVC(), tuned_parameters, scoring=scores, refit=refit_strategy
)
grid_search.fit(X_train, y_train)

通过我们的自定义策略，网格搜索选择的参数是：



In [ ]:
grid_search.best_params_

最后，我们在留出的评估集上评估微调后的模型： `grid_search` 对象 **已自动重新拟合** 到完整的训练集，并使用我们自定义的重新拟合策略选择的参数。

我们可以使用分类报告来计算留出集上的标准分类指标：



In [ ]:
from sklearn.metrics import classification_report

y_pred = grid_search.predict(X_test)
print(classification_report(y_test, y_pred))

.. NOTE::
问题太简单了：超参数平台过于平坦，输出模型在精度和召回率方面相同，质量上没有差异。

